# Практическая работа №1. Программная реализация вывода глубоких нейронных сетей для классификации изображений средствами нескольких фреймворков

## 1. Цели и задачи работы

**Цель работы** -- освоить методику анализа производительности вывода глубоких нейросетевых
моделей с использованием некоторого набора фреймворков на примере решения задачи классификации
изображений.

Достижение указанной цели предполагает решение следующих **задач**:

1. Формулировка задачи классификации изображений.
1. Выбор открытой модели для решения поставленной задачи. Изучение ее архитектуры.
1. Изучение программного интерфейса двух-трех фреймворков для вывода открытых
   нейросетевых моделей (PyTorch, TensorFlow, TensorFlow Lite, OpenVINO toolkit, другие).
   Выбор фреймворков зависит от формата модели, наличия необходимых конвертеров
   и возможности функционирования этих фреймворков на тестовой аппаратной платформе.
   Например, на RISC-V в настоящее время запускаются TensorFlow Lite и ncnn, также
   имеется неофициальный порт PyTorch, OpenVINO toolkit можно собрать из исходников
   (в ближайшее время будет оптимизирован под RISC-V).   
1. Программная реализация вывода выбранной модели с использованием изученных фреймворков.
1. Анализ качества решения задачи.
1. Анализ производительности вывода и определение оптимальных параметров запуска вывода
   на выбранной аппаратуре (размер пачки входных данных, количество потоков, другие).

## 2. Постановка задачи классификации изображений

**Задача классификации изображений** состоит в том, чтобы поставить в соответствие
изображению класс объектов, содержащихся на этом изображении. Формализуем постановку
задачи.

Исходное изображение, как правило, представляется набором интенсивностей пикселей

$$I=(I_{ij}^j)_{0 \le i < w, 0 \le j < h, 0 \le k < 3},$$

где $w$ и $h$ -- ширина и высота изображения, $k$ -- количество каналов,
а $I_{ij}^j$ -- значение интенсивности пикселя с пространственными координатами
$(i, j)$ по каналу $k$.

Предполагается, что определено множество наблюдаемых классов объектов на изображении:

$$C=\{0, 1,...,𝑁−1\}.$$

Множество идентификаторов классов однозначно соответствует множеству названий классов.
Таким образом, задача классификации изображений состоит в том, чтобы каждому
изображению поставить в соответствие класс, которому оно принадлежит:

$$\phi : I \rightarrow{} C.$$

## 3. Нейросетевая модель <НАЗВАНИЕ МОДЕЛИ>

<ОПИСАНИЕ АРХИТЕКТУРЫ ВЫБРАННОЙ МОДЕЛИ С УКАЗАНИЕМ КЛЮЧЕВЫХ ОСОБЕННОСТЕЙ>

## 4. Подготовка модели

### 4.1. Загрузка модели

<ОПИСАНИЕ, ОТКУДА И КАКИМ ОБРАЗОМ ЗАГРУЖЕНА МОДЕЛЬ>

ПРИМЕЧАНИЕ: ЕСЛИ МОДЕЛЬ ЗАГРУЖАЕТСЯ С ИСПОЛЬЗОВАНИЕМ ДОПОЛНИТЕЛЬНЫХ ПАКЕТОВ,
ТО УСТАНОВКА ЭТИХ ПАКЕТОВ ДОЛЖНА БЫТЬ ВЫПОЛНЕНА В ОТДЕЛЬНОЙ ВИРТУАЛЬНОЙ СРЕДЕ

### 4.2. Конвертация модели в формат <НАЗВАНИЕ ВЫБРАННОГО ФРЕЙМВОРКА 1>

<ОПИСАНИЕ ПОСЛЕДОВАТЕЛЬНОСТИ ДЕЙСТВИЙ, НЕОБХОДИМОЙ ДЛЯ КОНВЕРТАЦИИ МОДЕЛИ>

ПРИМЕЧАНИЕ: ДЛЯ КОНВЕРТАЦИИ МОДЕЛИ НЕОБХОДИМО СОЗДАВАТЬ ОТДЕЛЬНУЮ ВИРТУАЛЬНУЮ СРЕДУ

### 4.3. Конвертация модели в формат <НАЗВАНИЕ ВЫБРАННОГО ФРЕЙМВОРКА 2>

<ОПИСАНИЕ ПОСЛЕДОВАТЕЛЬНОСТИ ДЕЙСТВИЙ, НЕОБХОДИМОЙ ДЛЯ КОНВЕРТАЦИИ МОДЕЛИ>

ПРИМЕЧАНИЕ: ДЛЯ КОНВЕРТАЦИИ МОДЕЛИ НЕОБХОДИМО СОЗДАВАТЬ ОТДЕЛЬНУЮ ВИРТУАЛЬНУЮ СРЕДУ

## 5. Подготовка виртуальной среды для запуска экспериментов

<ОПИСАНИЕ ПОСЛЕДОВАТЕЛЬНОСТИ СОЗДАНИЯ ВИРТУАЛЬНОЙ СРЕДЫ ДЛЯ ПРОВЕДЕНИЯ ЭКСПЕРИМЕНТОВ
С ВЫБРАННЫМИ ФРЕЙМВОРКАМИ>

## 6. Программная реализация вспомогательных функций

### 6.1. Функции для вычисления показателей производительности

In [ ]:
# функция удаления заведомо некорректных времен
def delete_incorrect_time(times, min_correct_time=0.0):
    valid_times = []
    for i in range(len(times)):
        if times[i] >= min_correct_time:
            valid_times.append(times[i])
    return valid_times

# функция удаления времен, выходящих для пределы трех стандартных
# среднеквадратических отклонений (удаление выбросов)
def three_sigma_rule(times):
    average_time = np.mean(times)
    sigm = np.std(times)
    upper_bound = average_time + (3 * sigm)
    lower_bound = average_time - (3 * sigm)
    valid_times = []
    for i in range(len(times)):
        if lower_bound <= times[i] <= upper_bound:
            valid_times.append(times[i])
    return valid_times

# функция вычисления латентности - медианы набора корректных времен
def calculate_latency(times):
    latency = np.median(times)
    return latency

# функция вычисления метрики FPS - отношение произведения количества итераций
# и размера пачки данных к общему времени вывода
def calculate_fps(iter_num, batch_size, total_time):
    return iter_num * batch_size / total_time

# общая функция вычисления показателей производительности
def calculate_performance_metrics(times, batch_size, min_correct_time=0.0):
    valid_times = delete_incorrect_time(times, min_correct_time)
    valid_times = three_sigma_rule(valid_times)
    latency = calculate_latency(valid_times)
    fps = calculate_fps(len(valid_times), batch_size, sum(valid_times))
    return latency, fps

### 6.2. Функции обработки выхода классификационной сети

In [ ]:
# функция загрузки меток классов
def load_labels_map(labels_file_name):
    with open(labels_file_name, 'r') as f:
        labels_map = [line.strip() for line in f]
    return labels_map    

# функция печати topk-классов и соответствующих достоверностей
def process_output(files, output_data, labels_file_name, topk=5):
    labels_map = load_labels_map(labels_file_name)
    for i in range(len(output_data)):
        file_name = files[i]
        probs_ = np.squeeze(output_data[i])
        top_ind = np.argsort(probs_)[-topk:][::-1]
        print(f'{file_name}')
        for id_ in top_ind:
            det_label = labels_map[id_] if labels_map else '#{0}'.format(id_)
            print('\t{}\t{:.7f}\t{}'.format(id_, probs_[id_], det_label))

### 6.3. Чтение и предварительная обработка данных

Для чтения и подготовки изображений используется функционал библиотеки компьютерного
зрения OpenCV:

1. `cv2.imread(...)` -- функция, обеспечивающая загрузку изображения.
1. `cv2.resize(...)` -- функция, обеспечивающая масштабирование изображения
   в соответствии с размерами входного тензора нейронной сети.
1. <ВСТАВИТЬ ДРУГИЕ ФУНКЦИИ, КОТОРЫЕ ИСПОЛЬЗУЮТСЯ ДЛЯ ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ>

<ОПИСАНИЕ НАБОРА ДАННЫХ, КОТОРЫЙ ИСПОЛЬЗУЕТСЯ ДЛЯ ТЕСТИРОВАНИЯ>

In [ ]:
def prepare_input(images_dir, input_image_resolution, mean=(0, 0, 0),
                  scale=(1, 1, 1), bgr_to_rgb=False, show=False):
    files = [f for f in os.listdir(images_dir) if os.path.isfile(os.path.join(images_dir, f))]
    print(f'Number of available images: {len(files)}')
    images = []
    # <ВСТАВИТЬ ЧТЕНИЕ И ОБРАБОТКУ ИЗОБРАЖЕНИЙ>
    return files, images


## 7. Программная реализация вывода с использованием <НАЗВАНИЕ ФРЕЙМВОРКА 1>


### 7.1. Загрузка пакетов

In [ ]:
# <ЗАГРУЗКА НЕОБХОДИМЫХ ПАКЕТОВ ФРЕЙМВОРКА 1>

### 7.2. Загрузка и предварительная обработка данных

In [ ]:
# <ВЫЗОВ ФУНКЦИИ PREPARE_INPUT(...) ДЛЯ ЗАГРУЗКИ И ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ ИЗОБРАЖЕНИЙ>

### 7.3. Реализация вывода

In [ ]:
# <ПРОГРАММНАЯ РЕАЛИЗАЦИЯ ВЫВОДА СРЕДСТВАМИ ПРОГРАММНОГО ИНТЕРФЕЙСА ФРЕЙМВОРКА 1>

### 7.4. Запуск вывода и обработка результатов

In [ ]:
# количество повторений запуска вывода
iter_num = 100
# размер пачки данных
batch_size = 4

# функция многократного запуска вывода для фиксированного размера пачки
# и сбор результатов работы сети и времени работы каждого запроса на вывод
def inference_framework1(iter_num, batch_size, files, images):
    # список времен вывода для набора итераций
    times = []
    # словарь результатов вывода (ключ - название файла изображения,
    # значение - вектор достоверностей)
    results = dict()
    # из множества изображений организуется кольцевой буфер
    # индексы начального и конечного изображения в пачке данных
    istart = 0
    ifinish = batch_size
    for iteration in range(iter_num):
        # <ЗАПУСК ВЫВОДА ДЛЯ ПАЧКИ ИЗОБРАЖЕНИЙ>
        # <СОХРАНЕНИЕ РЕЗУЛЬТАТОВ ВЫВОДА В СЛОВАРЬ>
        # <СОХРАНЕНИЕ ВРЕМЕНИ ВЫВОДА В СПИСОК ВРЕМЕН>

        # пересчет индексов начального и конечного изображений для новой пачки
        istart = ifinish
        ifinish = (istart + batch_size) % (len(images) + 1)
        if istart > ifinish:
            istart = 0
            ifinish = batch_size
        
    return results, times

# функция запуска теста и вычисления показателей производительности вывода
def inference_framework1_perf(iter_num, batch_size, files, images):
    results, times = inference_framework1(iter_num, batch_size, files, images)
    latency, fps = calculate_performance_metrics(times, batch_size)
    return results, latency, fps


results, latency, fps = inference_framework1_perf(iter_num, batch_size, files, images)
print('Performance metrics:')
print(f'\tLatency: {latency:.3f} s\n\tFPS:     {fps:.2f} fps')

print('Results:')
for iteration in range(len(results)):
    process_output(results[iteration][0], results[iteration][1], labels_file_name, topk)

## 8. Программная реализация вывода с использованием <НАЗВАНИЕ ФРЕЙМВОРКА 2>

### 8.1. Загрузка пакетов

In [ ]:
# <ЗАГРУЗКА НЕОБХОДИМЫХ ПАКЕТОВ ФРЕЙМВОРКА 1>

### 8.2. Загрузка и предварительная обработка данных

In [ ]:
# <ВЫЗОВ ФУНКЦИИ PREPARE_INPUT(...) ДЛЯ ЗАГРУЗКИ И ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ ИЗОБРАЖЕНИЙ>

### 8.3. Реализация вывода

In [ ]:
# <ПРОГРАММНАЯ РЕАЛИЗАЦИЯ ВЫВОДА СРЕДСТВАМИ ПРОГРАММНОГО ИНТЕРФЕЙСА ФРЕЙМВОРКА 2>

### 8.4. Запуск вывода и обработка результатов

In [ ]:
# количество повторений запуска вывода
iter_num = 100
# размер пачки данных
batch_size = 4

# функция многократного запуска вывода для фиксированного размера пачки
# и сбор результатов работы сети и времени работы каждого запроса на вывод
def inference_framework2(iter_num, batch_size, files, images):
    # список времен вывода для набора итераций
    times = []
    # словарь результатов вывода (ключ - название файла изображения,
    # значение - вектор достоверностей)
    results = dict()
    # из множества изображений организуется кольцевой буфер
    # индексы начального и конечного изображения в пачке данных
    istart = 0
    ifinish = batch_size
    for iteration in range(iter_num):
        # <ЗАПУСК ВЫВОДА ДЛЯ ПАЧКИ ИЗОБРАЖЕНИЙ>
        # <СОХРАНЕНИЕ РЕЗУЛЬТАТОВ ВЫВОДА В СЛОВАРЬ>
        # <СОХРАНЕНИЕ ВРЕМЕНИ ВЫВОДА В СПИСОК ВРЕМЕН>

        # пересчет индексов начального и конечного изображений для новой пачки
        istart = ifinish
        ifinish = (istart + batch_size) % (len(images) + 1)
        if istart > ifinish:
            istart = 0
            ifinish = batch_size
        
    return results, times

# функция запуска теста и вычисления показателей производительности вывода
def inference_framework2_perf(iter_num, batch_size, files, images):
    results, times = inference_framework2(iter_num, batch_size, files, images)
    latency, fps = calculate_performance_metrics(times, batch_size)
    return results, latency, fps


results, latency, fps = inference_framework2_perf(iter_num, batch_size, files, images)
print('Performance metrics:')
print(f'\tLatency: {latency:.3f} s\n\tFPS:     {fps:.2f} fps')

print('Results:')
for iteration in range(len(results)):
    process_output(results[iteration][0], results[iteration][1], labels_file_name, topk)

## 9. Анализ качества решения задачи классификации

**Инструменты для сбора показателей качества.** <ОПИСАНИЕ ИСПОЛЬЗУЕМЫХ ИНСТРУМЕНТОВ>

**Набор данных.** <ОПИСАНИЕ НАБОРА ДАННЫХ>

**Показатели качества.** <ОПИСАНИЕ ПОКАЗАТЕЛЯ КАЧЕСТВА>

**Последовательность подготовки окружения и сбора показателей качества.** <ОПИСАНИЕ ПРОЦЕДУРЫ СБОРА ПОКАЗАТЕЛЕЙ КАЧЕСТВА> 

In [ ]:
# <ОТОБРАЖЕНИЕ ГИСТОГРАММЫ С ПОЛУЧЕННЫМИ РЕЗУЛЬТАТАМИ КАЧЕСТВА РЕШЕНИЯ ЗАДАЧИ КЛАССИФИКАЦИИ>
# <НЕОБХОДИМО ПОКАЗАТЬ РЕЗУЛЬТАТЫ ДЛЯ ФРЕЙМВОРКА 1, ФРЕЙМВОРКА 2 И РЕФЕНСНЫЕ ПОКАЗАТЕЛИ КАЧЕСТВА>

## 10. Анализ производительности вывода и определение оптимальных параметров запуска вывода

### 10.1. Параметры тестовой инфраструктуры

Для автоматического определения параметров тестовой инфраструктуры воспользуемся
возможностями пакетов `platform` и `openvino.runtime` по аналогии, как это сделано
в системе бенчмаркинга вывода DLI
([ссылка на ресурс](https://github.com/itlab-vision/dl-benchmark/blob/master/src/node_info/node_info.py)).

In [ ]:
import platform
import os
import subprocess
from collections import OrderedDict
from sys import version as python_formatted_version

try:
    from openvino.runtime import Core
    _ov_core_supported = True
except ImportError:
    _ov_core_supported = False

    
def get_cpu_name():
    cpuname = 'Undefined'

    if _ov_core_supported:
        core = Core()
        if 'CPU' in core.available_devices:
            cpuname = core.get_property('CPU', 'FULL_DEVICE_NAME')
        del core

    return cpuname.strip()

def get_gpu_name():
    gpuname = 'Undefined'

    if _ov_core_supported:
        core = Core()
        if 'GPU' in core.available_devices:
            gpuname = core.get_property('GPU', 'FULL_DEVICE_NAME')
        del core

    return gpuname

def get_ram_size(ostype):
    ramsize = 'Undefined'
    if ostype == 'Windows':
        command = ['wmic', 'OS', 'get', 'TotalVisibleMemorySize', '/Value']
        p = subprocess.Popen(command, universal_newlines=True, shell=True,
                             stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        text = p.stdout.read()
        p.wait()
        text = text.split('=')
        ramsize = text[1].strip() + ' KB'
    elif ostype == 'Linux':
        command = ['cat', '/proc/meminfo']
        all_info = subprocess.check_output(command).strip().decode()
        for line in all_info.split('\n'):
            if 'MemTotal' in line:
                return line.split(':')[1].strip()
    return ramsize

def get_system_characteristics():
    ostype = platform.system()
    characteristics = OrderedDict()
    characteristics.update({'CPU': get_cpu_name()})
    characteristics.update({'Number of CPUs': os.cpu_count()})
    characteristics.update({'CPU family': platform.processor()})
    characteristics.update({'GPU': get_gpu_name()})
    characteristics.update({'RAM size': get_ram_size(ostype)})
    characteristics.update({'OS family': platform.system()})
    characteristics.update({'OS version': platform.platform()})
    characteristics.update({'Python version': python_formatted_version})

    return characteristics


hardware_dict = get_system_characteristics()
for key, value in hardware_dict.items():
    print(f'{key:16}: {value}')

### 10.2. Параметры для перебора

In [ ]:
# размеры входных пачек данных
batch_sizes = [1, 2, 4, 8, 16]
# количество потоков
num_threads = [1, 2, 4, 8]
# количество итераций для определения показателей латентности и FPS
iter_num = 50
# устройство для запуска вывода
device = 'CPU'

### 10.3. Определение оптимальных параметров запуска вывода с использованием <НАЗВАНИЕ ФРЕЙМВОРКА 1>

In [ ]:
# <РЕАЛИЗОВАТЬ ФУНКЦИЮ ЗАПУСКА ТЕСТОВ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ РАЗНЫХ РАЗМЕРОВ ВХОДНЫХ ПАЧЕК ДАННЫХ>

Для наглядности полученных результатов производительности построим графики
зависимости латентности и FPS от размера пачки данных.

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ ЛАТЕНТНОСТИ ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Вывод из графика зависимости латентности от размера пачки данных:** <ДОБАВИТЬ ВЫВОДЫ>

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ FPS ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Выводы из графика зависимости FPS от размера пачки:** <ДОБАВИТЬ ВЫВОДЫ>

### 10.4. Определение оптимальных параметров запуска вывода с использованием <НАЗВАНИЕ ФРЕЙМВОРКА 2>

In [ ]:
# <РЕАЛИЗОВАТЬ ФУНКЦИЮ ЗАПУСКА ТЕСТОВ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ РАЗНЫХ РАЗМЕРОВ ВХОДНЫХ ПАЧЕК ДАННЫХ>

По аналогии для наглядности построим графики зависимости
латентности и FPS от размера пачки данных при разных значениях числа потоков.

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ ЛАТЕНТНОСТИ ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Вывод из графика зависимости латентности от пачки данных при разном числе потоков:** <ДОБАВИТЬ ВЫВОДЫ>

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ FPS ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Вывод из графика зависимости FPS от размера пачки данных**: <ДОБАВИТЬ ВЫВОДЫ>

### 10.5. Сравнение лучших показателей производительности

In [ ]:
# <ВЫБОР ЛУЧШИХ ПОКАЗАТЕЛЕЙ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ КАЖДОГО ФРЕЙМВОРКА>

**Вывод из полученных результатов:** <ДОБАВИТЬ ВЫВОДЫ>